In [1]:
%load_ext autoreload
%autoreload 2

In [2]:
import sys
import os
import json
import pickle

from matplotlib import pyplot as plt
%matplotlib inline
from IPython.display import clear_output
from tqdm.autonotebook import tqdm
import trimesh
import numpy as np
import torch

/opt/conda/lib/python3.6/site-packages/ipykernel_launcher.py:9: TqdmExperimentalWarning: Using `tqdm.autonotebook.tqdm` in notebook mode. Use `tqdm.tqdm` instead to force console mode (e.g. in jupyter console)
  if __name__ == '__main__':


In [3]:
sys.path.append('../')
from shapefit.deform.src.deformation.deformation import Deformer
from shapefit.deform.src.data_proc.voxels import read_shapenet_voxels
from shapefit.deform.src.deformation.utils import (
    set_new_mesh_vertices,
    add_noise_to_mesh,
    mesh_pcloud,
    filter_edges_by_parts,
    sphere
)
from shapefit.deform.src.deformation.preproc import find_sharp_edges, split_vertices_by_parts, transform_voxels_to_origin, \
    filter_voxels_by_clustering, neighboring_scene_voxel_parts, filter_scene_voxel_parts_with_obb, level_merger, \
    find_corresondences_with_obb
from shapefit.deform.src.deformation.utils import rot_x, rot_y, rot_z, translate, scale, compose

In [4]:
DATA_DIR = '../data'
ASSETS_DIR = '/home/ishvlad/workspace/Scan2CAD/Assets'
INPUT_DIR = os.path.join(ASSETS_DIR, 'full/benchmarks/E2E/deformation-input')
SHAPENET_DIR = os.path.join(ASSETS_DIR, 'full/shapenet')

In [5]:
with open(os.path.join(DATA_DIR, 'sharp_features/sharp_edges.json'), 'r') as readfile:
    sharp_edges = json.load(readfile)
with open(os.path.join(DATA_DIR, 'sharp_features/sharp_vertices.json'), 'r') as readfile:
    sharp_vertices = json.load(readfile)

In [6]:
scene_id = 'scene0535_00'
scene_voxels = read_shapenet_voxels(INPUT_DIR, scene_id)
scene_shape_id = 2
data_object = scene_voxels[scene_shape_id]

In [7]:
MESH_REMESHED = os.path.join(SHAPENET_DIR, 
                             data_object['shapenet_id'], 
                             data_object['object_id'],
                             'models/model_normalized_remeshed_5.obj')
mesh_remeshed = trimesh.load(MESH_REMESHED)
transform = data_object['transform']

In [8]:
with open(os.path.join(SHAPENET_DIR,
                       data_object['shapenet_id'],
                       data_object['object_id'],
                       'models/partnet_map_5.pkl'), 'rb') as read_file:
    partnet_map = pickle.load(read_file)
all_parts = sorted(list(set([partnet_map[k][0] for k in partnet_map])))
cmap = {}
for part in all_parts:
    cmap[part] = np.zeros(4).astype(int)
    cmap[part][:3] = np.random.randint(0, 255, (3,))
for k in partnet_map:
    mesh_remeshed.visual.vertex_colors[k] = cmap[partnet_map[k][0]]

In [9]:
part_sharp_edges_ids = find_sharp_edges(mesh_remeshed, data_object, sharp_edges, partnet_map)
parts_idx = split_vertices_by_parts(all_parts, partnet_map)
voxel_centers_p2p, surface_samples_p2p = transform_voxels_to_origin(data_object, all_parts, transform, parts_idx)
voxel_centers_p2p = filter_voxels_by_clustering(voxel_centers_p2p)
neighboring_voxel_centers_ids = neighboring_scene_voxel_parts(voxel_centers_p2p)
voxel_centers_p2p = filter_scene_voxel_parts_with_obb(voxel_centers_p2p, neighboring_voxel_centers_ids)
voxel_centers_nn, surface_samples_nn = find_corresondences_with_obb(voxel_centers_p2p, mesh_remeshed, parts_idx, make_bbox_transform=True)

In [10]:
part_clouds = []
for i, part in enumerate(all_parts):
    pcloud_color = cmap[part]
    if len(voxel_centers_p2p[i]) > 0:
        pcloud = mesh_pcloud(voxel_centers_p2p[i], size=0.005, color=pcloud_color)
        part_clouds += [pcloud]

In [11]:
pcloud_voxel_nn = mesh_pcloud(voxel_centers_nn, size=0.005, color=[255, 0, 0, 0])
pcloud_surface_nn = mesh_pcloud(mesh_remeshed.vertices[surface_samples_nn], size=0.005, color=[0, 255, 0, 0])

In [12]:
mesh_and_cloud_nn = trimesh.util.concatenate([mesh_remeshed, pcloud_voxel_nn, pcloud_surface_nn])
mesh_and_cloud_nn.show()

In [13]:
mesh_and_cloud_p2p = trimesh.util.concatenate([mesh_remeshed, *part_clouds])
mesh_and_cloud_p2p.show()

In [14]:
transform = translate([0, 0, 0])
print(transform)

In [16]:
parts = [mesh_remeshed]
initial_vertices_transforms = [torch.Tensor(np.repeat(transform[None, :, :], len(parts[0].vertices), axis=0)) for 
                               part in parts]
initial_vertices_transforms = torch.cat(initial_vertices_transforms, dim=0)

noise = np.random.normal(size=(len(mesh_remeshed.vertices), 3), scale=0.00001)
noisy_part = add_noise_to_mesh(mesh_remeshed, noise)
noisy_parts = [noisy_part]

In [17]:
noisy_part.show()

In [69]:
deformer = Deformer(noisy_part,
                    initial_vertices_transforms,
                    sigma=0.07,
                    voxel_centers_nn=voxel_centers_nn,
                    surface_samples_nn=surface_samples_nn,
                    voxel_centers_p2p=voxel_centers_p2p,
                    surface_samples_p2p=surface_samples_p2p,
                    sharp_edges=part_sharp_edges_ids,
                    kernel='ep_kernel',
                    mapping='nn',
                    cuda=None,
                    device_mode='cpu',
                    deg_thr=1e-10,
                    ampl_factor=10)

initializing parts descriptions...
computing bitriangles maps...
computing faces-to-edges maps...
computing adjacent edges for each face...
[Num flat edges (before): 401 ]
[Num flat edges (after): 1 ]
[Number of vertices (before): 10000 ]
[Number of vertices (after): 10401 ]
computing edges deformations...
constructing soft indicators...
initialization done


In [19]:
initial_vertices = deformer.get_initial_parts_vertices()
initial_mesh = set_new_mesh_vertices(noisy_part, initial_vertices)
color = np.array([255, 0, 0, 0])
for facet in initial_mesh.facets:
    initial_mesh.visual.face_colors[facet] = color

In [20]:
shape_to_compare = trimesh.util.concatenate([mesh_remeshed, initial_mesh])
shape_to_compare.show()

In [ ]:
output = deformer.solve_data(alpha_0=0,
                             alpha_reg=1e-6,
                             alpha_sharp=0,
                             alpha_data_nn=1e2,
                             alpha_data_p2p=0,
                             alpha_quad=1,
                             iterations=200,
                             lr=1,
                             print_freq=5,
                             use_precond=True,
                             hessian_cpu=True,
                             load_hessian_path=None,
                             plot=False)

In [93]:
first_approximation = deformer.get_first_approximation()
initial_vertices = deformer.get_initial_parts_vertices()

In [94]:
initial_mesh = set_new_mesh_vertices(noisy_part, initial_vertices)
color = np.array([255, 0, 0, 0])
for facet in initial_mesh.facets:
    initial_mesh.visual.face_colors[facet] = color

In [95]:
approximation_mesh = set_new_mesh_vertices(noisy_part, first_approximation)
color = np.array([0, 255, 0, 0])
for facet in approximation_mesh.facets:
    approximation_mesh.visual.face_colors[facet] = color

In [ ]:
shape_to_compare = trimesh.util.concatenate([approximation_mesh, initial_mesh, mesh_remeshed])
shape_to_compare.show()